In [1]:
# Import all the libraries required

import soccerdata as sd
import pandas as pd
from tqdm import tqdm
import ScraperFC as sfc
import traceback

import warnings

# from pyspark.sql import SparkSession
# from pyspark.sql.types import StructType, StructField, StringType
# import pyspark.pandas as ps


[02/03/24 15:38:59] INFO     No custom team name replacements found. You can configure these in       ]8;id=929552;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_config.py\_config.py]8;;\:]8;id=459389;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_config.py#87\87]8;;\
                             C:\Users\ksbha\soccerdata\config\teamname_replacements.json.                          

                    INFO     No custom league dict found. You can configure additional leagues in    ]8;id=112762;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_config.py\_config.py]8;;\:]8;id=961474;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_config.py#165\165]8;;\
                             C:\Users\ksbha\soccerdata\config\league_dict.json.                                    

In [2]:
import datetime

In [3]:
## Create a connection to Snowflake
from sqlalchemy import create_engine
import snowflake.connector

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\options.py:103: UserWarning: You have an incompatible version of 'pyarrow' installed (14.0.2), please install a version that adheres to: 'pyarrow<10.1.0,>=10.0.1; extra == "pandas"'
  warn_incompatible_dep(


[02/03/24 15:39:00] WARNING  Failed to import ArrowResult. No Apache Arrow result set format can be    ]8;id=919233;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=725949;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#94\94]8;;\
                             used. ImportError: DLL load failed while importing arrow_iterator: The                
                             specified procedure could not be found.                                               

In [4]:
import snowflake.connector
from snowflake.connector.pandas_tools import write_pandas

In [5]:
# spark = SparkSession.builder \
#     .master("local") \
#     .appName("Gegenstats") \
#     .getOrCreate()

In [6]:
## Set options to view all columns
pd.set_option('display.max_columns', None)

In [7]:
# spark.conf.set("spark.sql.execution.arrow.pyspark.enabled", "true")

In [16]:
scraper = sfc.Understat()
def scrape_league_data(league_years):
    output_df = pd.DataFrame(columns=['№', 'Team', 'M', 'W', 'D', 'L', 'G', 'GA', 'PTS', 'xG', 'NPxG', 'xGA',
       'NPxGA', 'NPxGD', 'PPDA', 'OPPDA', 'DC', 'ODC', 'xPTS', 'season','league'])
    for league_year in league_years:
        try:
            ooper = scraper.scrape_league_table(year=league_year[1], league=league_year[0])
            season_val = league_year[1]
            ooper['season'] = int(str(int(str(season_val)[2:])-1)+str(season_val)[2:])
            if league_year[0] == 'EPL':
                ooper['league'] = 'ENG-Premier League'
            output_df = pd.concat([output_df, ooper])
            
        except Exception as e:
            print(f"An error occurred for the year {league_years}: {e}")
            traceback.print_exc()
    scraper.close()
    return output_df

league_years = [('EPL', 2022),('EPL', 2023), ('EPL', 2024)]  # Replace with your list of years
out = scrape_league_data(league_years)

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\ScraperFC\Understat.py:361: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  columns = pd.read_html(table)[0].columns
d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\ScraperFC\Understat.py:366: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  df = pd.read_html(table)[0]
C:\Users\ksbha\AppData\Local\Temp\ipykernel_10932\3767552972.py:12: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  output_df = pd.concat([output_df, ooper])
d:\Users\ksbha\mi

In [17]:
understat_table = out[['league','Team','season', 'W', 'D', 'L','G','GA', 'xG', 'xGA','NPxG','NPxGA','PPDA',
                       'OPPDA','PTS','xPTS']]

In [18]:
understat_table.loc[understat_table['Team'] == 'Manchester United', 'Team'] = 'Manchester Utd'
understat_table.loc[understat_table['Team'] == 'Newcastle United', 'Team'] = 'Newcastle Utd'
understat_table.loc[understat_table['Team'] == 'Tottenham Hotspur', 'Team'] = 'Tottenham'
understat_table.loc[understat_table['Team'] == 'Wolverhampton Wanderers', 'Team'] = 'Wolves'
understat_table.loc[understat_table['Team'] == 'Nottingham Forest', 'Team'] = "Nott'ham Forest"
understat_table.loc[understat_table['Team'] == 'Leicester', 'Team'] = 'Leicester City'
understat_table.loc[understat_table['Team'] == 'Leeds', 'Team'] = 'Leeds United'
understat_table.loc[understat_table['Team'] == 'Sheffield United', 'Team'] = "Sheffield Utd"
# understat_table.loc[understat_table['Team'] == 'Luton Town', 'Team'] = 'Luton'
understat_table.loc[understat_table['Team'] == 'Norwich', 'Team'] = 'Norwich City'

In [19]:
understat_table.sort_values(by=['league','season','Team'], ascending=True, inplace=True)
understat_table.reset_index(drop=True, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_10932\614021855.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  understat_table.sort_values(by=['league','season','Team'], ascending=True, inplace=True)


In [20]:
understat_table.rename(columns={'Team':'TEAM_NAME', 'W':'TEAM_WINS', 'D':'TEAM_DRAWS', 'league':'COMPETITION',
                                'L': 'TEAM_LOSSES', 'xPTS':'TEAM_XPTS', 'PTS':'TEAM_PTS', 'season':'SEASON',
                                'NPxGA':'NPXG_AGAINST', 'xGA':'XG_AGAINST'}, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_10932\2521636844.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  understat_table.rename(columns={'Team':'TEAM_NAME', 'W':'TEAM_WINS', 'D':'TEAM_DRAWS', 'league':'COMPETITION',


In [21]:
understat_table.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [12]:
fbref = sd.FBref(leagues="ENG-Premier League", seasons=["2122","2223","2324"])
fbref_team_standard = fbref.read_team_season_stats(stat_type='standard')
# fbref_team_standard_oppo = fbref.read_team_season_stats(stat_type='standard', opponent_stats=True)
fbref_team_shooting = fbref.read_team_season_stats(stat_type='shooting')
fbref_team_shooting_oppo = fbref.read_team_season_stats(stat_type='shooting', opponent_stats=True)
fbref_team_passing = fbref.read_team_season_stats(stat_type='passing')
fbref_team_passing_oppo = fbref.read_team_season_stats(stat_type='passing', opponent_stats=True)
fbref_team_defense = fbref.read_team_season_stats(stat_type='defense')
fbref_team_possession = fbref.read_team_season_stats(stat_type='possession')
fbref_team_misc = fbref.read_team_season_stats(stat_type='misc')
fbref_keeper = fbref.read_team_season_stats(stat_type='keeper')
fbref_schedule = fbref.read_schedule()
fbref_lineups = fbref.read_lineup()

[02/03/24 15:42:14] INFO     Saving cached data to C:\Users\ksbha\soccerdata\data\FBref               ]8;id=880624;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_common.py\_common.py]8;;\:]8;id=784276;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_common.py#91\91]8;;\

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:674: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)
d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:674: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[02/03/24 15:42:28] INFO     [1/979] Retrieving game with id=3adf2aa7                                  ]8;id=397161;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=89809;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#878\878]8;;\

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:893: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_table.loc[:bench_idx, "is_starter"] = True
d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:893: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_table.loc[:bench_idx, "is_starter"] = True


                    INFO     [2/979] Retrieving game with id=4eb36e37                                  ]8;id=605474;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=700641;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#878\878]8;;\

...

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:893: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_table.loc[:bench_idx, "is_starter"] = True
d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:893: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_table.loc[:bench_idx, "is_starter"] = True


                    INFO     [978/979] Retrieving game with id=16dc9951                                ]8;id=600511;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=792190;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#878\878]8;;\

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:893: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_table.loc[:bench_idx, "is_starter"] = True
d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:893: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_table.loc[:bench_idx, "is_starter"] = True


                    INFO     [979/979] Retrieving game with id=457203bc                                ]8;id=486949;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=72413;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#878\878]8;;\

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:893: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_table.loc[:bench_idx, "is_starter"] = True
d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:893: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_table.loc[:bench_idx, "is_starter"] = True


In [13]:
fbref_lineups.replace({"Jarrell Quansah": "Jarell Quansah"}, inplace=True)
fbref_lineups.replace({"Omotayo Adaramola": "Tayo Adaramola"}, inplace=True)

In [14]:
fbref_lineups.loc[fbref_lineups['team'] == 'Brighton & Hove Albion', 'team'] = 'Brighton'
fbref_lineups.loc[fbref_lineups['team'] == 'Manchester United', 'team'] = 'Manchester Utd'
fbref_lineups.loc[fbref_lineups['team'] == 'Newcastle United', 'team'] = 'Newcastle Utd'
fbref_lineups.loc[fbref_lineups['team'] == 'Nottingham Forest', 'team'] = "Nott'ham Forest"
fbref_lineups.loc[fbref_lineups['team'] == 'Sheffield United', 'team'] = "Sheffield Utd"
fbref_lineups.loc[fbref_lineups['team'] == 'Tottenham Hotspur', 'team'] = 'Tottenham'
fbref_lineups.loc[fbref_lineups['team'] == 'West Ham United', 'team'] = 'West Ham'
fbref_lineups.loc[fbref_lineups['team'] == 'Wolverhampton Wanderers', 'team'] = 'Wolves'

In [15]:
fbref_team_standard = fbref_team_standard.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
# fbref_team_standard_oppo = fbref_team_standard_oppo.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_shooting = fbref_team_shooting.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_shooting_oppo = fbref_team_shooting_oppo.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_passing = fbref_team_passing.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_passing_oppo = fbref_team_passing_oppo.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_defense = fbref_team_defense.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_possession = fbref_team_possession.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_misc = fbref_team_misc.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_keeper = fbref_keeper.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_schedule = fbref_schedule.rename_axis(index={'season': 'SEASON', 'league': 'COMPETITION'})
fbref_lineups = fbref_lineups.rename_axis(index={'season': 'SEASON', 'league': 'COMPETITION'})
fbref_lineups.rename({'team': 'TEAM_NAME'}, axis=1, inplace=True)

In [16]:
## Get rid of incomplete games (Thank God Tom Lockyear is good <3)
fbref_schedule = fbref_schedule.dropna(subset=['home_xg'])

## Get rid of 'vs ' in the TEAM_NAME column
fbref_team_passing_oppo.reset_index(inplace=True)
fbref_team_shooting_oppo.reset_index(inplace=True)

In [17]:
fbref_team_passing_oppo['TEAM_NAME'] = fbref_team_passing_oppo['TEAM_NAME'].str.replace('vs ', '')
fbref_team_shooting_oppo['TEAM_NAME'] = fbref_team_shooting_oppo['TEAM_NAME'].str.replace('vs ', '')

fbref_team_passing_oppo.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)
fbref_team_shooting_oppo.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [18]:
# Convert the date column to datetime format
fbref_schedule['date'] = pd.to_datetime(fbref_schedule['date'])
# fbref_schedule = fbref_schedule[fbref_schedule['date'] < datetime.datetime(2023, 12, 20)]

fbref_schedule = fbref_schedule[fbref_schedule['date'] <= datetime.datetime.now().strftime('%Y-%m-%d')]

In [19]:
def make_season_integer(df):
    indexes = df.index.names
    df = df.reset_index()
    df['SEASON'] = df['SEASON'].astype(int)
    df = df.set_index(indexes)
    return df

fbref_team_standard = make_season_integer(fbref_team_standard)
# fbref_team_standard_oppo = make_season_integer(fbref_team_standard_oppo)
fbref_team_shooting = make_season_integer(fbref_team_shooting)
fbref_team_shooting_oppo = make_season_integer(fbref_team_shooting_oppo)
fbref_team_passing = make_season_integer(fbref_team_passing)
fbref_team_passing_oppo = make_season_integer(fbref_team_passing_oppo)
fbref_team_defense = make_season_integer(fbref_team_defense)
fbref_team_possession = make_season_integer(fbref_team_possession)
fbref_team_misc = make_season_integer(fbref_team_misc)
fbref_schedule = make_season_integer(fbref_schedule)
fbref_keeper = make_season_integer(fbref_keeper)
fbref_lineups = make_season_integer(fbref_lineups)

In [30]:
team_matches_played = fbref_team_standard['Playing Time'].MP
team_goals_scored = understat_table.G
team_npxG_90 = fbref_team_standard['Per 90 Minutes'].npxG
team_goals_conceded = understat_table.GA
# team_xG_against_90 = fbref_team_standard_oppo['Per 90 Minutes'].xG
team_shots = fbref_team_shooting['Standard'].Sh
team_shotsOT = fbref_team_shooting['Standard'].SoT
team_pass_completed = fbref_team_passing["Total"].Cmp
team_pass_attempted = fbref_team_passing["Total"].Att
team_tackles = fbref_team_defense.Tackles.Tkl
team_tackles_won = fbref_team_defense.Tackles.TklW
team_takeons_attempted = fbref_team_possession['Take-Ons'].Att
team_takeons_completed = fbref_team_possession['Take-Ons'].Succ
team_crossesintoPA = fbref_team_passing['CrsPA']
team_fouls_against = fbref_team_misc['Performance']['Fld']
team_fouls_made = fbref_team_misc['Performance']['Fls']
team_interceptions = fbref_team_defense['Int']
team_blocks_shots = fbref_team_defense['Blocks'].Sh
team_blocks_pass = fbref_team_defense['Blocks'].Pass
team_clearances = fbref_team_defense.Clr
team_aerials_won = fbref_team_misc['Aerial Duels'].Won
team_aerials_lost = fbref_team_misc['Aerial Duels'].Lost
team_shots_faced = fbref_team_shooting_oppo['Standard'].Sh

In [31]:
team_recoveries= fbref_team_misc['Performance']['Recov']

In [32]:
teams_poss_won = team_interceptions + team_tackles_won + team_recoveries + team_blocks_shots + \
    team_blocks_pass + team_aerials_won
team_OPPDA = understat_table['OPPDA']
team_final_3rd_passes_against =  fbref_team_passing_oppo['1/3']
team_cleansheets = fbref_keeper['Performance']['CS']

In [45]:
team_names = fbref_team_standard.reset_index()[['TEAM_NAME','url']]
team_names['TEAM_FBREF_ID'] = team_names['url'].apply(lambda x: x.split('/')[3])      ## Extracting team_id from URL
team_names.drop(columns=['url'], inplace=True)
team_names.columns = team_names.columns.droplevel(1)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_25680\2026419047.py:3: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  team_names.drop(columns=['url'], inplace=True)


In [46]:
team_names['TEAM_FBREF_ID'] = team_names['TEAM_FBREF_ID'].astype('string')

In [47]:
team_names.drop_duplicates(inplace=True)

## WHoScored Data

In [8]:
ws = sd.WhoScored(leagues='ENG-Premier League', seasons=["2122","2223","2324"], headless=False)

[02/03/24 15:39:54] INFO     Saving cached data to C:\Users\ksbha\soccerdata\data\WhoScored           ]8;id=999023;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_common.py\_common.py]8;;\:]8;id=447735;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_common.py#91\91]8;;\

[02/03/24 15:39:55] INFO     patching driver executable                                              ]8;id=313680;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\undetected_chromedriver\patcher.py\patcher.py]8;;\:]8;id=758032;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\undetected_chromedriver\patcher.py#346\346]8;;\
                             C:\Users\ksbha\appdata\roaming\undetected_chromedriver\undetected_chrom               
                             edriver.exe                                                                           

In [9]:
ws_schedule = ws.read_schedule()

[02/03/24 15:40:00] INFO     Retrieving game schedule of ENG-Premier League - 2122 from the cache  ]8;id=916679;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=513122;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#437\437]8;;\

                    INFO     Retrieving game schedule of ENG-Premier League - 2223 from the cache  ]8;id=541579;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=337556;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#437\437]8;;\

[02/03/24 15:40:06] INFO     Scraping game schedule from                                           ]8;id=227459;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=969418;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#427\427]8;;\
                             https://www.whoscored.com/Regions/252/Tournaments/2/Seasons/9618/Engl                 
                             and-Premier-League                                                                    

                    INFO     Scraping game schedule for Thursday, Feb 1 2024                       ]8;id=540134;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=825652;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

                    INFO     Scraping game schedule for Saturday, Feb 3 2024                       ]8;id=500996;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=427464;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

...

                    INFO     Scraping game schedule for Sunday, Aug 20 2023                        ]8;id=178350;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=250376;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

                    INFO     Scraping game schedule for Monday, Aug 21 2023                        ]8;id=22208;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=751063;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

                    INFO     Scraping game schedule for Friday, Aug 25 2023                        ]8;id=670985;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=182010;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

                    INFO     Scraping game schedule for Saturday, Aug 26 2023                      ]8;id=179691;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=94383;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

[02/03/24 15:41:02] INFO     Scraping game schedule for Sunday, Aug 27 2023                        ]8;id=543782;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=259862;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

In [10]:
ws_schedule = ws_schedule[ws_schedule['date'] <= datetime.datetime.now().strftime('%Y-%m-%d')]

In [20]:
fbref_schedule = fbref_schedule.dropna(subset=['home_xg'])

In [21]:
ws_schedule = ws_schedule.reset_index().rename({'league':"COMPETITION", "season":"SEASON"}, axis=1)
ws_schedule.set_index(['COMPETITION', 'SEASON', 'game'], inplace=True)

In [23]:
ws_schedule.loc[ws_schedule['home_team'] == 'Manchester United', 'home_team'] = 'Manchester Utd'
ws_schedule.loc[ws_schedule['away_team'] == 'Manchester United', 'away_team'] = 'Manchester Utd'
ws_schedule.loc[ws_schedule['home_team'] == 'Newcastle United', 'home_team'] = 'Newcastle Utd'
ws_schedule.loc[ws_schedule['away_team'] == 'Newcastle United', 'away_team'] = 'Newcastle Utd'
ws_schedule.loc[ws_schedule['home_team'] == 'Newcastle', 'home_team'] = 'Newcastle Utd'
ws_schedule.loc[ws_schedule['away_team'] == 'Newcastle', 'away_team'] = 'Newcastle Utd'
ws_schedule.loc[ws_schedule['home_team'] == 'Tottenham Hotspur', 'home_team'] = 'Tottenham'
ws_schedule.loc[ws_schedule['away_team'] == 'Tottenham Hotspur', 'away_team'] = 'Tottenham'
ws_schedule.loc[ws_schedule['home_team'] == 'Wolverhampton Wanderers', 'home_team'] = 'Wolves'
ws_schedule.loc[ws_schedule['away_team'] == 'Wolverhampton Wanderers', 'away_team'] = 'Wolves'
ws_schedule.loc[ws_schedule['home_team'] == 'Wolverhampton', 'home_team'] = 'Wolves'
ws_schedule.loc[ws_schedule['away_team'] == 'Wolverhampton', 'away_team'] = 'Wolves'
ws_schedule.loc[ws_schedule['home_team'] == 'Nottingham Forest', 'home_team'] = "Nott'ham Forest"
ws_schedule.loc[ws_schedule['away_team'] == 'Nottingham Forest', 'away_team'] = "Nott'ham Forest"
ws_schedule.loc[ws_schedule['home_team'] == 'Leicester', 'home_team'] = "Leicester City"
ws_schedule.loc[ws_schedule['away_team'] == 'Leicester', 'away_team'] = "Leicester City"
ws_schedule.loc[ws_schedule['home_team'] == 'Leeds', 'home_team'] = "Leeds United"
ws_schedule.loc[ws_schedule['away_team'] == 'Leeds', 'away_team'] = "Leeds United"
ws_schedule.loc[ws_schedule['home_team'] == 'Sheffield United', 'home_team'] = "Sheffield Utd"
ws_schedule.loc[ws_schedule['away_team'] == 'Sheffield United', 'away_team'] = "Sheffield Utd"
ws_schedule.loc[ws_schedule['home_team'] == 'Luton', 'home_team'] = "Luton Town"
ws_schedule.loc[ws_schedule['away_team'] == 'Luton', 'away_team'] = "Luton Town"
ws_schedule.loc[ws_schedule['home_team'] == 'Norwich', 'home_team'] = "Norwich City"
ws_schedule.loc[ws_schedule['away_team'] == 'Norwich', 'away_team'] = "Norwich City"

In [24]:
ws_schedule.reset_index(inplace=True)
fbref_schedule.reset_index(inplace=True)

In [25]:
ws_schedule = ws_schedule.rename({'game_id':"ws_game_id"}, axis=1)

In [26]:
ws_schedule['SEASON'] = ws_schedule['SEASON'].astype('int64')

In [27]:
fbref_schedule = pd.merge(fbref_schedule, ws_schedule[["COMPETITION", "SEASON", "home_team", "away_team","ws_game_id"]], 
          on=["COMPETITION", "SEASON", "home_team", "away_team"], how='inner')

In [ ]:
loader = ws.read_events(output_fmt='loader')

[01/31/24 14:07:40] INFO     Retrieving game schedule of ENG-Premier League - 2122 from the cache  ]8;id=881330;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=352107;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#437\437]8;;\

                    INFO     Retrieving game schedule of ENG-Premier League - 2223 from the cache  ]8;id=726684;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=757031;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#437\437]8;;\

[01/31/24 14:07:46] INFO     Scraping game schedule from                                           ]8;id=9722;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=744750;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#427\427]8;;\
                             https://www.whoscored.com/Regions/252/Tournaments/2/Seasons/9618/Engl                 
                             and-Premier-League                                                                    

                    INFO     Scraping game schedule for Monday, Jan 1 2024                         ]8;id=3129;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=951072;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

                    INFO     Scraping game schedule for Tuesday, Jan 2 2024                        ]8;id=462408;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=535714;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

...

                    INFO     [972/976] Retrieving game with id=1549901                             ]8;id=997494;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=652951;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

                    INFO     [973/976] Retrieving game with id=1729211                             ]8;id=869149;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=631917;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

                    INFO     [974/976] Retrieving game with id=1729261                             ]8;id=313383;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=31883;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

                    INFO     [975/976] Retrieving game with id=1549710                             ]8;id=796746;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=926141;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

                    INFO     [976/976] Retrieving game with id=1640784                             ]8;id=229480;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=354833;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

In [28]:
game_ids = ws_schedule['ws_game_id'].unique()

In [29]:
ws_players = pd.DataFrame(columns=['game_id', 'team_id', 'player_id', 'player_name', 
                                   'is_starter','minutes_played', 'jersey_number', 'starting_position'])

In [ ]:
for game in tqdm(game_ids):
    ws_players = pd.concat([ws_players, loader.players(game_id=game)])

 99%|█████████▉| 968/973 [00:47<00:00, 20.58it/s]


TypeError: 'NoneType' object is not subscriptable

In [ ]:
ws_players.head()

game_id team_id player_id      player_name is_starter minutes_played  \
0  1549539     189    276366       David Raya       True             97   
1  1549539     189    342499    Ethan Pinnock       True             97   
2  1549539     189    321085  Kristoffer Ajer       True             72   
3  1549539     189    121123   Pontus Jansson       True             97   
4  1549539     189    295964      Sergi Canós       True             97   

  jersey_number starting_position  
0             1                GK  
1             5                DC  
2            20                DC  
3            18                DC  
4             7               DMR

In [ ]:
## WhoScored decide to name Willy Boly with two different names. Idiots
ws_players.replace({"Willy-Arnaud Boly": "Willy Boly"}, inplace=True)
ws_players.replace({"Kepa": "Kepa Arrizabalaga"}, inplace=True)
ws_players.replace({"Yehor Yarmolyuk": "Yehor Yarmoliuk"}, inplace=True)
ws_players.replace({"Vitalii Mykolenko": "Vitaliy Mykolenko"}, inplace=True)
ws_players.replace({"Dan Bentley": "Daniel Bentley"}, inplace=True)
ws_players.replace({"Toti": "Toti Gomes"}, inplace=True)
ws_players.replace({"Joe Hodge": "Joseph Hodge"}, inplace=True)
ws_players.replace({"Jonny Otto": "Jonny"}, inplace=True)
ws_players.replace({"Álvaro Carreras": "Álvaro Fernández"}, inplace=True)
ws_players.replace({"Alisson Becker": "Alisson"}, inplace=True)
ws_players.replace({"Andy Robertson": "Andrew Robertson"}, inplace=True)
ws_players.replace({"Konstantinos Tsimikas": "Kostas Tsimikas"}, inplace=True)
ws_players.replace({"Alphonse Aréola": "Alphonse Areola"}, inplace=True)
ws_players.replace({"Pape Sarr": "Pape Matar Sarr"}, inplace=True)
ws_players.replace({"Yago Alonso": "Yago Santiago"}, inplace=True)

## Snowflake Data Upload

In [30]:
SNOWFLAKE_USER = 'kbharaj3'
SNOWFLAKE_PASSWORD = 'Snowfl@key0014'
SNOWFLAKE_ACCOUNT = 'qx25653.ca-central-1.aws'
SNOWFLAKE_WAREHOUSE = 'FOOTY_STORE'
SNOWFLAKE_DATABASE = 'GEGENSTATS'
SNOWFLAKE_SCHEMA = 'TABLES'

In [31]:
conn = snowflake.connector.connect(
    user=SNOWFLAKE_USER,
    password=SNOWFLAKE_PASSWORD,
    account=SNOWFLAKE_ACCOUNT,
    warehouse=SNOWFLAKE_WAREHOUSE,
    database=SNOWFLAKE_DATABASE,
    schema=SNOWFLAKE_SCHEMA
    )

[02/03/24 15:52:06] INFO     Snowflake Connector for Python Version: 3.3.1, Python Version:       ]8;id=395722;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py\connection.py]8;;\:]8;id=950655;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py#334\334]8;;\
                             3.11.5, Platform: Windows-10-10.0.22000-SP0                                           

                    INFO     This connection is in OCSP Fail Open Mode. TLS Certificates would   ]8;id=913787;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py\connection.py]8;;\:]8;id=626940;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py#1103\1103]8;;\
                             be checked for validity and revocation status. Any other                              
                             Certificate Revocation related exceptions or OCSP Responder                           
                             failures would be disregarded in favor of connectivity.                               

                    INFO     Setting use_openssl_only mode to False                              ]8;id=724435;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py\connection.py]8;;\:]8;id=819641;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py#1121\1121]8;;\

In [32]:
cur = conn.cursor()
cur.execute(f"USE WAREHOUSE {SNOWFLAKE_WAREHOUSE}")

[02/03/24 15:52:07] INFO     query: [USE WAREHOUSE FOOTY_STORE]                                       ]8;id=314749;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=840643;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

[02/03/24 15:52:08] INFO     query execution done                                                     ]8;id=976246;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=881004;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=228566;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=926553;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [33]:
create_schema_sql = f"CREATE SCHEMA IF NOT EXISTS {SNOWFLAKE_SCHEMA}"
cur.execute(create_schema_sql)

                    INFO     query: [CREATE SCHEMA IF NOT EXISTS TABLES]                              ]8;id=889950;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=664808;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=31049;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=745598;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=702166;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=132754;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [34]:
print("The Snowflake warehouse being used is:", SNOWFLAKE_WAREHOUSE)

The Snowflake warehouse being used is: FOOTY_STORE


In [ ]:
create_table_query = """
CREATE TABLE IF NOT EXISTS TEAMS (
	TEAM_NAME VARCHAR(255),
	TEAM_FBREF_ID VARCHAR(255) PRIMARY KEY,
    TEAM_LOGO_URL VARCHAR(255)
);
"""

In [ ]:
cur.execute(create_table_query)

In [77]:
def insert_to_snowflake_DB(primary_keys, table_name, dataframe, replace=False):
    if replace:
        cur.execute(f"TRUNCATE TABLE {table_name}")
        success, nchunks, nrows, _ = write_pandas(conn, dataframe, table_name)
    else:
        cur.execute(f"SELECT {', '.join(primary_keys)} FROM {table_name}")
        existing_ids = cur.fetchall()
        existing_ids = [id for id in existing_ids]
        dataframe.set_index(primary_keys, inplace=True)
        new_rows = dataframe[~dataframe.index.isin(existing_ids)]
        new_rows.reset_index(inplace=True)
        dataframe.reset_index(inplace=True)
        if not new_rows.empty:
            success, nchunks, nrows, _ = write_pandas(conn, new_rows, table_name)
            print(f"Inserted {nrows} new rows")
        else:
            print("No new rows to insert")

In [ ]:
team_logos = \
[["18bb7c10", "https://i.imgur.com/SURo5sj.png"], ["8602292d", "https://i.imgur.com/M4mwH1X.png"],
 ["4ba7cbea", "https://i.imgur.com/0F6UIO4.png"], ["cd051869", "https://i.imgur.com/MOhGOQ4.png"],
 ["d07537b9", "https://i.imgur.com/EMCwD3X.png"], ["cff3d9bb", "https://i.imgur.com/6F7h3UR.png"],
 ["47c64c55", "https://i.imgur.com/LPhzr0K.png"], ["d3fd31cc", "https://i.imgur.com/Dgei0uj.png"],
 ["fd962109", "https://i.imgur.com/2zggSrF.png"], ["5bfb9659", "https://i.imgur.com/2tipH85.png"],
 ["a2d435b3", "https://i.imgur.com/ldOUO84.png"], ["822bd0ba", "https://i.imgur.com/fs7VK9G.png"],
 ["b8fd03ef", "https://i.imgur.com/FF8z7uZ.png"], ["19538871", "https://i.imgur.com/z47emBQ.png"],
 ["b2b47a98", "https://i.imgur.com/3kOLokZ.png"], ["e4a775cb", "https://i.imgur.com/z4Tl9Zu.png"],
 ["33c895d4", "https://i.imgur.com/35GrgJC.png"], ["361ca564", "https://i.imgur.com/fJ7rUWW.png"],
 ["7c21e445", "https://i.imgur.com/9BQHJRl.png"], ["8cec06e1", "https://i.imgur.com/6azSF88.png"]
 ]

In [ ]:
df_logos = pd.DataFrame(team_logos, columns=['TEAM_FBREF_ID', 'TEAM_LOGO'])

In [48]:
team_names = team_names.merge(df_logos, on='TEAM_FBREF_ID', how='left')

NameError: name 'df_logos' is not defined

In [49]:
team_names.rename(columns={'TEAM_LOGO':'TEAM_LOGO_URL'}, inplace=True)

In [ ]:
insert_to_snowflake_DB(['TEAM_FBREF_ID'], 'TEAMS', team_names, replace=True)

In [ ]:
team_names.drop(columns=['TEAM_LOGO_URL'], inplace=True)

In [ ]:
create_standard_team_stats_query = """
CREATE TABLE IF NOT EXISTS TEAM_STANDARD_STATS (
    TEAM_FBREF_ID VARCHAR(255),
    SEASON INT,
    COMPETITION VARCHAR(255),
    MATCHES_PLAYED INT,
    TEAM_WINS INT,
    TEAM_DRAWS INT,
    TEAM_LOSSES INT,
    TEAM_PTS INT,
    TEAM_XPTS DOUBLE,
    PRIMARY KEY (TEAM_FBREF_ID, COMPETITION, SEASON),
    FOREIGN KEY (TEAM_FBREF_ID) REFERENCES GEGENSTATS.TABLES.TEAMS(TEAM_FBREF_ID)
);
"""

In [ ]:
cur.execute(create_standard_team_stats_query)

In [ ]:
team_standard_stats = understat_table.copy()

In [ ]:
team_standard_stats['MATCHES_PLAYED'] = team_matches_played

In [ ]:
team_standard_stats.reset_index(inplace=True)

In [ ]:
## Merge team_matches_played with team_names to get TEAM_ID
team_standard_stats = team_standard_stats.merge(team_names, on='TEAM_NAME', how='left')

In [ ]:
team_standard_stats = team_standard_stats[['TEAM_FBREF_ID','SEASON','COMPETITION','MATCHES_PLAYED','TEAM_WINS', 
                                           'TEAM_DRAWS', 'TEAM_LOSSES', 'TEAM_PTS', 'TEAM_XPTS']]

In [ ]:
insert_to_snowflake_DB(['TEAM_FBREF_ID', 'COMPETITION','SEASON'], 'TEAM_STANDARD_STATS', team_standard_stats, replace=True)

In [ ]:
create_team_attacking_stats_query = """
CREATE TABLE IF NOT EXISTS TEAM_ATTACKING_STATS (
    TEAM_FBREF_ID VARCHAR(255),
    SEASON INT,
    COMPETITION VARCHAR(255),
    GOALS_SCORED INT,
    NPXG DOUBLE,
    XG DOUBLE,
    SHOTS INT,
    SHOTS_ON_TARGET INT,
    PASS_COMPLETED INT,
    PASS_ATTEMPTED INT,
    TAKEONS_ATTEMPTED INT,
    TAKEONS_COMPLETED INT,
    CROSSES_INTO_PA INT,
    FOULS_AGAINST INT,
    PRIMARY KEY (TEAM_FBREF_ID, COMPETITION, SEASON),
    FOREIGN KEY (TEAM_FBREF_ID) REFERENCES GEGENSTATS.TABLES.TEAMS(TEAM_FBREF_ID)
);
"""

In [ ]:
cur.execute(create_team_attacking_stats_query)

In [ ]:
team_attacking_stats = understat_table.copy()

In [ ]:
team_attacking_stats = team_attacking_stats.reset_index().merge(team_names, on='TEAM_NAME', how='left')

In [ ]:
team_attacking_stats = team_attacking_stats[['TEAM_NAME','TEAM_FBREF_ID','COMPETITION','SEASON','NPxG','xG']]

In [ ]:
team_attacking_stats.head()

In [ ]:
team_attacking_stats.rename(columns={'NPxG': 'NPXG', 'xG':'XG'}, inplace=True)

In [ ]:
team_attacking_stats.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [ ]:
team_attacking_stats['GOALS_SCORED'] = team_goals_scored
team_attacking_stats['SHOTS'] = team_shots
team_attacking_stats['SHOTS_ON_TARGET'] = team_shotsOT
team_attacking_stats['PASS_COMPLETED'] = team_pass_completed
team_attacking_stats['PASS_ATTEMPTED'] = team_pass_attempted
team_attacking_stats['TAKEONS_ATTEMPTED'] = team_takeons_attempted
team_attacking_stats['TAKEONS_COMPLETED'] = team_takeons_completed
team_attacking_stats['CROSSES_INTO_PA'] = team_crossesintoPA
team_attacking_stats['FOULS_AGAINST'] = team_fouls_against

In [ ]:
team_attacking_stats.reset_index(inplace=True)
team_attacking_stats.drop(columns=['TEAM_NAME'], inplace=True)

In [ ]:
insert_to_snowflake_DB(['TEAM_FBREF_ID', 'COMPETITION','SEASON'], 'TEAM_ATTACKING_STATS', team_attacking_stats,replace=True)

In [ ]:
create_team_defending_stats_query = """
CREATE TABLE IF NOT EXISTS TEAM_DEFENDING_STATS (
    TEAM_FBREF_ID VARCHAR(255),
    SEASON INT,
    COMPETITION VARCHAR(255),
    GOALS_CONCEDED INT,
    XG_AGAINST DOUBLE,
    NPXG_AGAINST DOUBLE,
    TACKLES INT,
    TACKLES_WON INT,
    FOULS_MADE INT,
    INTERCEPTIONS INT,
    BLOCKED_SHOTS INT,
    BLOCKED_PASSES INT,
    CLEARANCES INT,
    PPDA DOUBLE,
    OPP_PPDA DOUBLE,               -- New field for Opponent's PPDA
    FINAL_3RD_PASSES_AGAINST INT,  -- New field for Final Third Passes Against
    POSS_WON INT,                  -- New field for Possession Won
    CLEAN_SHEETS INT,              -- New field for Clean Sheets
    PRIMARY KEY (TEAM_FBREF_ID, COMPETITION, SEASON),
    FOREIGN KEY (TEAM_FBREF_ID) REFERENCES GEGENSTATS.TABLES.TEAMS(TEAM_FBREF_ID)
);
"""

In [ ]:
cur.execute(create_team_defending_stats_query)

In [ ]:
team_defending_stats = understat_table.copy()

In [ ]:
team_defending_stats = team_defending_stats.reset_index().merge(team_names, on='TEAM_NAME', how='left')

In [ ]:
team_defending_stats = team_defending_stats[['TEAM_NAME','TEAM_FBREF_ID','COMPETITION','SEASON']]

In [ ]:
team_defending_stats.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [ ]:
team_defending_stats['GOALS_CONCEDED'] = team_goals_conceded
team_defending_stats['XG_AGAINST'] = understat_table['XG_AGAINST']
team_defending_stats['NPXG_AGAINST'] = understat_table['NPXG_AGAINST']
team_defending_stats['TACKLES'] = team_tackles
team_defending_stats['TACKLES_WON'] = team_tackles_won
team_defending_stats['FOULS_MADE'] = team_fouls_made
team_defending_stats['INTERCEPTIONS'] = team_interceptions
team_defending_stats['BLOCKED_SHOTS'] = team_blocks_shots
team_defending_stats['BLOCKED_PASSES'] = team_blocks_pass
team_defending_stats['CLEARANCES'] = team_clearances
team_defending_stats['PPDA'] = understat_table['PPDA']

In [ ]:
team_defending_stats.reset_index(inplace=True)
team_defending_stats.drop(columns=['TEAM_NAME'], inplace=True)

In [ ]:
insert_to_snowflake_DB(['TEAM_FBREF_ID','COMPETITION','SEASON'], 'TEAM_DEFENDING_STATS', team_defending_stats,
                       replace=True)

In [ ]:
create_team_misc_stats_query = """
CREATE TABLE IF NOT EXISTS TEAM_MISC_STATS (
    TEAM_FBREF_ID VARCHAR(255),
    SEASON INT,
    COMPETITION VARCHAR(255),
    AERIALS_WON INT,
    AERIALS_LOST INT,
    PRIMARY KEY (TEAM_FBREF_ID, COMPETITION, SEASON),
    FOREIGN KEY (TEAM_FBREF_ID) REFERENCES GEGENSTATS.TABLES.TEAMS(TEAM_FBREF_ID)
);
"""

In [ ]:
cur.execute(create_team_misc_stats_query)

In [ ]:
team_misc_stats = understat_table.copy()

In [ ]:
team_misc_stats = team_misc_stats.reset_index().merge(team_names, on='TEAM_NAME', how='left')

In [ ]:
team_misc_stats = team_misc_stats[['TEAM_NAME','TEAM_FBREF_ID','COMPETITION','SEASON']]

In [ ]:
team_misc_stats.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [ ]:
team_misc_stats['AERIALS_WON'] = team_aerials_won
team_misc_stats['AERIALS_LOST'] = team_aerials_lost

In [ ]:
team_misc_stats.reset_index(inplace=True)
team_misc_stats.drop(columns=['TEAM_NAME'], inplace=True)

In [ ]:
insert_to_snowflake_DB(['TEAM_FBREF_ID', 'COMPETITION', 'SEASON'], 'TEAM_MISC_STATS', team_misc_stats, replace=True)

# Now, inclusion of Match, Season and Competition data

In [ ]:
create_competition_query = """
CREATE TABLE IF NOT EXISTS COMPETITIONS (
    COMPETITION VARCHAR(255),
    COMPETITION_NAME VARCHAR(255),
    COMPETITION_ACRONYM VARCHAR(255),
    SEASON INT,
    PRIMARY KEY (COMPETITION, SEASON)
);
"""

In [ ]:
cur.execute(create_competition_query)

In [ ]:
df_competitions = fbref_schedule.reset_index()[['COMPETITION', 'SEASON']].drop_duplicates().copy()

In [ ]:
df_competitions['COMPETITION_NAME'] = ''
df_competitions['COMPETITION_ACRONYM'] = ''

In [ ]:
df_competitions.loc[df_competitions['COMPETITION'] == 'ENG-Premier League', 'COMPETITION_NAME'] = 'English Premier League'
df_competitions.loc[df_competitions['COMPETITION'] == 'ENG-Premier League', 'COMPETITION_ACRONYM'] = 'EPL'

In [ ]:
insert_to_snowflake_DB(['COMPETITION','SEASON'], 'COMPETITIONS', df_competitions, replace=True)

In [ ]:
create_season_query = """
CREATE TABLE IF NOT EXISTS SEASONS (
	SEASON INT PRIMARY KEY,
    SEASON_NAME VARCHAR(255),
    START_YEAR INT,
    END_YEAR INT
);
"""

In [ ]:
cur.execute(create_season_query)

In [ ]:
df_seasons = df_competitions[['SEASON']].copy()

In [ ]:
df_seasons['SEASON_NAME'] = ''
df_seasons['START_YEAR'] = 0
df_seasons['END_YEAR'] = 0

In [ ]:
df_seasons.loc[df_seasons['SEASON'] == 2223, 'SEASON_NAME'] = '2022-2023'
df_seasons.loc[df_seasons['SEASON'] == 2223, 'START_YEAR'] = 2022
df_seasons.loc[df_seasons['SEASON'] == 2223, 'END_YEAR'] = 2023

In [ ]:
insert_to_snowflake_DB(['SEASON'], 'SEASONS', df_seasons, replace=True)

In [ ]:
create_stadium_query = """
CREATE TABLE IF NOT EXISTS STADIUMS (
	STADIUM VARCHAR(255),
    TEAM_FBREF_ID VARCHAR(255),
    SEASON INT,
    PRIMARY KEY (TEAM_FBREF_ID, STADIUM, SEASON)
);
"""

In [ ]:
cur.execute(create_stadium_query)

In [ ]:
df_stadiums = fbref_schedule.reset_index()[['home_team', 'SEASON',
            'venue']].drop_duplicates().rename(columns={'home_team': 'TEAM_NAME', 'venue': 'STADIUM'})

In [ ]:
df_stadiums = df_stadiums.merge(team_names, on='TEAM_NAME')[['STADIUM','SEASON','TEAM_FBREF_ID']]

In [ ]:
insert_to_snowflake_DB(['TEAM_FBREF_ID','STADIUM', 'SEASON'], 'STADIUMS', df_stadiums, replace=True)

In [43]:
create_match_query = """
CREATE TABLE IF NOT EXISTS MATCHES (
    MATCH_ID VARCHAR(255) PRIMARY KEY,
    DATE_TIME VARCHAR(255), 
    HOME_TEAM_ID VARCHAR(255),
    AWAY_TEAM_ID VARCHAR(255),
    COMPETITION VARCHAR(255),
    SEASON INT,
    STADIUM VARCHAR(255),
    GAMEWEEK INT,
    DAY VARCHAR(255),
    HOME_TEAM_SCORE INT,
    AWAY_TEAM_SCORE INT,
    HOME_TEAM_XG DOUBLE,
    AWAY_TEAM_XG DOUBLE,
    ATTENDANCE INT,
    REFEREE VARCHAR(255),
    WS_MATCH_ID INT UNIQUE NOT NULL,
    FOREIGN KEY (HOME_TEAM_ID) REFERENCES GEGENSTATS.TABLES.TEAMS(TEAM_FBREF_ID),
    FOREIGN KEY (AWAY_TEAM_ID) REFERENCES GEGENSTATS.TABLES.TEAMS(TEAM_FBREF_ID),
    FOREIGN KEY (COMPETITION, SEASON) REFERENCES GEGENSTATS.TABLES.COMPETITIONS(COMPETITION, SEASON),
    FOREIGN KEY (SEASON) REFERENCES GEGENSTATS.TABLES.SEASONS(SEASON),
    FOREIGN KEY (HOME_TEAM_ID, STADIUM, SEASON) REFERENCES GEGENSTATS.TABLES.STADIUMS(TEAM_FBREF_ID, STADIUM, SEASON)
);
"""

In [53]:
cur.execute(create_match_query)

[01/31/24 13:43:26] INFO     query: [CREATE TABLE IF NOT EXISTS MATCHES ( MATCH_ID VARCHAR(255)       ]8;id=429939;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=65494;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             PRIMARY KEY, DATE_TIM...]                                                             

[01/31/24 13:43:27] INFO     query execution done                                                     ]8;id=630744;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=783102;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=781578;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=943221;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [43]:
df_matches = fbref_schedule.reset_index()[['game_id', 'date', 'time', 'home_team', 'away_team', 'COMPETITION', 'SEASON', 'venue',
                                           'week', 'day', 'score', 'home_xg', 'away_xg', 'attendance', 'referee', 'ws_game_id']]

In [50]:
df_matches = df_matches.merge(team_names.rename(columns={'TEAM_FBREF_ID': 'home_team_id', 
                                                         'TEAM_NAME': 'home_team'}), on='home_team', how='left')

In [51]:
df_matches = df_matches.merge(team_names.rename(columns={'TEAM_FBREF_ID': 'away_team_id', 
                                                         'TEAM_NAME': 'away_team'}), on='away_team', how='left')

In [52]:
# Combine df_matches date and time to a dt.datatime configuration
df_matches['date'] = df_matches['date'].astype(str)
df_matches['time'] = df_matches['time'].astype(str)
df_matches['date_time'] = df_matches['date'] + ' ' + df_matches['time']
df_matches['date_time'] = pd.to_datetime(df_matches['date_time'])

In [53]:
# Split score in df_matches by "-" to home_team_score and away_team_score 
df_matches[['home_team_score', 'away_team_score']] = df_matches['score'].str.split('–', expand=True)

In [57]:
df_matches.rename(columns={'game_id': 'MATCH_ID', 'date_time': 'DATE_TIME', 'home_team_id': 'HOME_TEAM_ID', 'away_team_id': 'AWAY_TEAM_ID',
                           'venue': 'STADIUM', 'week': 'GAMEWEEK', 'day': 'DAY','home_team_score': 'HOME_TEAM_SCORE', 
                           'away_team_score':'AWAY_TEAM_SCORE', 'home_xg':'HOME_TEAM_XG','away_xg':'AWAY_TEAM_XG',
                           'attendance':'ATTENDANCE', 'referee': 'REFEREE', 'ws_game_id':'WS_MATCH_ID'}, inplace=True)

In [58]:
df_matches.drop(columns=['date', 'time', 'home_team', 'away_team', 'score'], inplace=True)

In [59]:
df_matches['DATE_TIME'] = df_matches['DATE_TIME'].astype('string')

In [59]:
insert_to_snowflake_DB(['MATCH_ID'], 'MATCHES', df_matches, replace=True)

[01/31/24 13:44:07] INFO     query: [TRUNCATE TABLE MATCHES]                                          ]8;id=896311;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=46949;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=139747;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=93503;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=77144;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=790596;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=150355;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=113966;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=897286;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=157383;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[01/31/24 13:44:08] INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=65660;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=819681;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=703543;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=573838;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [COPY INTO "MATCHES" /*                                           ]8;id=284594;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=69489;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */...]                         

[01/31/24 13:44:10] INFO     query execution done                                                     ]8;id=425844;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=244385;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=357189;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=883668;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

TIme to deal with event data!

In [35]:
ws_event_spadl = ws.read_events(output_fmt='spadl')

[02/03/24 15:52:39] INFO     Retrieving game schedule of ENG-Premier League - 2122 from the cache  ]8;id=279175;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=637707;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#437\437]8;;\

                    INFO     Retrieving game schedule of ENG-Premier League - 2223 from the cache  ]8;id=111126;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=497783;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#437\437]8;;\

[02/03/24 15:52:45] INFO     Scraping game schedule from                                           ]8;id=32263;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=482064;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#427\427]8;;\
                             https://www.whoscored.com/Regions/252/Tournaments/2/Seasons/9618/Engl                 
                             and-Premier-League                                                                    

                    INFO     Scraping game schedule for Thursday, Feb 1 2024                       ]8;id=594664;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=810864;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

                    INFO     Scraping game schedule for Saturday, Feb 3 2024                       ]8;id=244182;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=183659;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#327\327]8;;\

...

                    INFO     [1015/1019] Retrieving game with id=1640938                           ]8;id=396326;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=884006;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

                    INFO     [1016/1019] Retrieving game with id=1640853                           ]8;id=334409;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=412049;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

                    INFO     [1017/1019] Retrieving game with id=1640731                           ]8;id=379071;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=219847;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

                    INFO     [1018/1019] Retrieving game with id=1640746                           ]8;id=764990;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=431749;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

[02/03/24 16:03:16] INFO     [1019/1019] Retrieving game with id=1729496                           ]8;id=650164;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=957011;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#693\693]8;;\

In [36]:
old_events = ws_event_spadl.copy()

In [37]:
import socceraction.spadl as spadl

In [38]:
ws_event_spadl.loc[ws_event_spadl['team'] == 'Manchester United', 'team'] = 'Manchester Utd'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Newcastle United', 'team'] = 'Newcastle Utd'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Newcastle', 'team'] = 'Newcastle Utd'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Tottenham Hotspur', 'team'] = 'Tottenham'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Wolverhampton Wanderers', 'team'] = 'Wolves'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Wolverhampton', 'team'] = 'Wolves'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Nottingham Forest', 'team'] = "Nott'ham Forest"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Leicester', 'team'] = "Leicester City"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Leeds', 'team'] = "Leeds United"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Sheffield United', 'team'] = "Sheffield Utd"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Sheff Utd', 'team'] = "Sheffield Utd"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Luton', 'team'] = "Luton Town"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Norwich', 'team'] = "Norwich City"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Man City', 'team'] = "Manchester City"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Man Utd', 'team'] = "Manchester Utd"

In [39]:
cur.execute('SELECT * FROM TEAMS')
team_rows = cur.fetchall()
column_names = [desc[0] for desc in cur.description]
curr_team_names = pd.DataFrame(team_rows, columns=column_names)

[02/03/24 16:04:39] INFO     query: [SELECT * FROM TEAMS]                                             ]8;id=147527;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=622241;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

[02/03/24 16:04:40] INFO     query execution done                                                     ]8;id=402061;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=744946;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 25                                     ]8;id=291854;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=636074;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [40]:
ws_event_spadl = ws_event_spadl.merge(spadl.actiontypes_df(), how="left").merge(spadl.bodyparts_df(), how="left")

In [67]:
## Add a Team_id for WhoScored to the Table "Team"
# cur.execute("""ALTER TABLE GEGENSTATS.TABLES.TEAMS
# ADD COLUMN TEAM_WS_ID INT UNIQUE;""")

In [41]:
ws_event_spadl.rename({'game_id':'WS_MATCH_ID', 'original_event_id':'ORIGINAL_EVENT_ID','period_id':'PERIOD_ID',
                       'time_seconds':'TIME_SECONDS', 'team_id':'TEAM_WS_ID', 'player_id':'PLAYER_WS_ID', 'start_x':'START_X',
                        'end_x':'END_X', 'start_y':'START_Y', 'end_y':'END_Y','type_name':'TYPE_NAME',
                        'bodypart_name':'BODYPART_NAME','result_id':'RESULT_ID', 'action_id':'ACTION_ID'}, axis=1, inplace=True)

In [60]:
ws_event_spadl = ws_event_spadl.merge(df_matches[['MATCH_ID', 'WS_MATCH_ID']], on='WS_MATCH_ID')

In [61]:
ws_event_spadl = ws_event_spadl.merge(curr_team_names[['TEAM_FBREF_ID','TEAM_WS_ID']], on='TEAM_WS_ID')

In [63]:
ws_event_spadl.rename({'TEAM_FBREF_ID':'team_id','START_X':'start_x','START_Y':'start_y','END_X':'end_x','END_Y':'end_y'}, axis=1,
                      inplace=True)

In [64]:
# old_events2 = ws_event_spadl.copy()

In [65]:
for index, row in df_matches.iterrows():
    inds_to_replace = ws_event_spadl[ws_event_spadl['MATCH_ID'] == row['MATCH_ID']].index
    ws_event_spadl.loc[inds_to_replace] = spadl.play_left_to_right(ws_event_spadl.loc[inds_to_replace], row['HOME_TEAM_ID'])

In [68]:
ws_event_spadl.rename({'team_id':'TEAM_FBREF_ID','start_x':'START_X','start_y':'START_Y','end_x':'END_X','end_y':'END_Y'}, axis=1,
                      inplace=True)

In [69]:
ws_event_spadl['NEW_TIME_SECONDS'] = ws_event_spadl['TIME_SECONDS']

In [70]:
ws_event_spadl_period1 = ws_event_spadl[ws_event_spadl['PERIOD_ID'] == 1]
ws_event_spadl_period2 = ws_event_spadl[ws_event_spadl['PERIOD_ID'] == 2]

In [71]:
start_time_2nd_half = ws_event_spadl_period2.groupby(['MATCH_ID', 'PERIOD_ID'])['NEW_TIME_SECONDS'].min().reset_index()

In [72]:
for index, row in tqdm(start_time_2nd_half.iterrows()):
    time_to_remove = row['NEW_TIME_SECONDS']
    ws_event_spadl.loc[(ws_event_spadl['MATCH_ID'] == row['MATCH_ID']) & (ws_event_spadl['PERIOD_ID'] == 2), 'NEW_TIME_SECONDS'] -= time_to_remove

978it [01:29, 10.89it/s]


In [74]:
create_events_spadl_query = """
CREATE TABLE IF NOT EXISTS EVENTS_SPADL (
    MATCH_ID VARCHAR(255),
    ORIGINAL_EVENT_ID BIGINT,
    PERIOD_ID INT,
    TIME_SECONDS FLOAT,
    NEW_TIME_SECONDS FLOAT,
    TEAM_FBREF_ID VARCHAR(255),
    PLAYER_WS_ID INT,
    START_X FLOAT,
    END_X FLOAT,
    START_Y FLOAT,
    END_Y FLOAT,
    RESULT_ID INT,
    ACTION_ID INT,
    TYPE_NAME VARCHAR(255),
    BODYPART_NAME VARCHAR(255),
    PRIMARY KEY (MATCH_ID, ACTION_ID),
    FOREIGN KEY (MATCH_ID) REFERENCES GEGENSTATS.TABLES.MATCHES(MATCH_ID),
    FOREIGN KEY (PLAYER_WS_ID) REFERENCES GEGENSTATS.TABLES.PLAYERS(PLAYER_WS_ID),
    FOREIGN KEY (TEAM_FBREF_ID) REFERENCES GEGENSTATS.TABLES.TEAMS(TEAM_FBREF_ID)
);
"""

In [75]:
cur.execute(create_events_spadl_query)

[02/03/24 16:15:17] INFO     query: [CREATE TABLE IF NOT EXISTS EVENTS_SPADL ( MATCH_ID VARCHAR(255), ]8;id=445012;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=161353;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             ORIGINAL_EVENT_...]                                                                   

                    INFO     query execution done                                                     ]8;id=322825;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=330300;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=461261;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=839452;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [78]:
insert_to_snowflake_DB(['MATCH_ID','ACTION_ID'], 'EVENTS_SPADL', 
                       ws_event_spadl.drop(['type_id', 'player', 'team', 'WS_MATCH_ID', 'TEAM_WS_ID','bodypart_id'],axis=1), 
                       replace=True)

[02/03/24 16:15:47] INFO     query: [TRUNCATE TABLE EVENTS_SPADL]                                     ]8;id=959638;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=878772;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=636259;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=690356;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=202621;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=986394;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=220197;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=702045;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=740985;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=73468;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[02/03/24 16:15:52] INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=418992;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=609404;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=431097;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=106954;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

[02/03/24 16:15:56] INFO     query: [COPY INTO "EVENTS_SPADL" /*                                      ]8;id=360400;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=284394;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas...]                              

[02/03/24 16:16:12] INFO     query execution done                                                     ]8;id=411575;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=223916;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=283986;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=675084;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

### Create a "Players" table in Snowflake

In [72]:
## Sort out "Players" "Table
ws_players.rename({'team_id':'TEAM_WS_ID', 'game_id':'WS_MATCH_ID'}, axis=1, inplace=True)

In [73]:
ws_players = ws_players.merge(curr_team_names, on="TEAM_WS_ID", how="left")

In [74]:
ws_players = ws_players.sort_values(by=["WS_MATCH_ID","TEAM_NAME","jersey_number"])

In [75]:
fbref_lineups.merge(curr_team_names[['TEAM_NAME','TEAM_FBREF_ID','TEAM_WS_ID']], on='TEAM_NAME')

jersey_number                  player      TEAM_NAME  is_starter  \
0                  1              David Raya      Brentford        True   
1                  3              Rico Henry      Brentford        True   
2                  5           Ethan Pinnock      Brentford        True   
3                  6      Christian Nørgaard      Brentford        True   
4                  7             Sergi Canós      Brentford        True   
...              ...                     ...            ...         ...   
38686             16          Oliver Norwood  Sheffield Utd       False   
38687             23              Ben Osborn  Sheffield Utd       False   
38688             33  Rhys Norrington-Davies  Sheffield Utd       False   
38689             38             Femi Seriki  Sheffield Utd       False   
38690             40             Jili Buyabu  Sheffield Utd       False   

      position  minutes_played TEAM_FBREF_ID  TEAM_WS_ID  
0           GK              90      cd051869         189  
1           WB              90      cd051869         189  
2           CB              90      cd051869         189  
3           CM              90      cd051869         189  
4           WB              90      cd051869         189  
...        ...             ...           ...         ...  
38686       DM               3      1df6b87e         163  
38687     <NA>               0      1df6b87e         163  
38688       LB              11      1df6b87e         163  
38689     <NA>               0      1df6b87e         163  
38690     <NA>               0      1df6b87e         163  

[38691 rows x 8 columns]

In [76]:
fbref_lineups = fbref_lineups.reset_index().merge(fbref_schedule.reset_index()[['game', 'game_id','ws_game_id']], how='right', on='game')

In [77]:
fbref_lineups = fbref_lineups.rename({'ws_game_id':'WS_MATCH_ID'}, axis=1)

In [78]:
# fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Brighton & Hove Albion', 'TEAM_NAME'] = 'Brighton'
# fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Manchester United', 'TEAM_NAME'] = 'Manchester Utd'
# fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Newcastle United', 'TEAM_NAME'] = 'Newcastle Utd'
# fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Nottingham Forest', 'TEAM_NAME'] = "Nott'ham Forest"
# fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Sheffield United', 'TEAM_NAME'] = "Sheffield Utd"
# fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Tottenham Hotspur', 'TEAM_NAME'] = 'Tottenham'
# fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'West Ham United', 'TEAM_NAME'] = 'West Ham'
# fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Wolverhampton Wanderers', 'TEAM_NAME'] = 'Wolves'

In [79]:
fbref_lineups = fbref_lineups.merge(curr_team_names[['TEAM_NAME','TEAM_FBREF_ID','TEAM_WS_ID']], on='TEAM_NAME')

In [80]:
ws_players.rename({'player_id':'WS_player_id', 'player_name':'WS_player_name','minutes_played':'WS_minutes_played',
                   'starting_position':'WS_starting_position', 'is_starter':'WS_is_starter'}, axis=1, inplace=True)

In [81]:
fbref_lineups.rename({'minutes_played':'FBREF_minutes_played', 'game_id':'MATCH_ID','position':'FBREF_position',
                      'is_starter':'FBREF_is_starter'}, axis=1, inplace=True)

In [82]:
fbref_lineups = fbref_lineups.merge(ws_players, on=["TEAM_FBREF_ID", "TEAM_NAME", "WS_MATCH_ID",
                                                    "TEAM_WS_ID", "jersey_number"])

In [83]:
df_players = fbref_lineups[['WS_player_id', 'player', 'WS_player_name']].drop_duplicates()

In [84]:
df_players.rename({'WS_player_id':'PLAYER_WS_ID', 'player':'PLAYER_FBREF_NAME', 'WS_player_name':'PLAYER_WS_NAME'}, 
                  axis=1, inplace=True)

In [72]:
create_players_query = """
CREATE TABLE IF NOT EXISTS PLAYERS (
    PLAYER_WS_ID INT,
    PLAYER_FBREF_NAME VARCHAR(255),
    PLAYER_WS_NAME VARCHAR(255),
    PRIMARY KEY (PLAYER_WS_ID)
);
"""

In [73]:
cur.execute(create_players_query)

[01/27/24 17:34:52] INFO     query: [CREATE TABLE IF NOT EXISTS PLAYERS ( PLAYER_WS_ID INT,           ]8;id=447576;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=654003;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             PLAYER_FBREF_NAME VARCHAR...]                                                         

                    INFO     query execution done                                                     ]8;id=443465;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=344417;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=719860;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=407893;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [74]:
insert_to_snowflake_DB(['PLAYER_WS_ID'], 'PLAYERS', df_players,replace=True)

[01/27/24 17:34:55] INFO     query: [TRUNCATE TABLE PLAYERS]                                          ]8;id=264367;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=297447;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=205559;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=394398;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=634664;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=296184;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

C:\Users\ksbha\AppData\Local\Temp\ipykernel_8416\2303712821.py:4: UserWarning: Pandas Dataframe has non-standard index of type <class 'pandas.core.indexes.base.Index'> which will not be written. Consider changing the index to pd.RangeIndex(start=0,...,step=1) or call reset_index() to keep index as column(s)
  success, nchunks, nrows, _ = write_pandas(conn, dataframe, table_name)


                    INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=960516;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=947613;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

...

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=50098;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=772885;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=686430;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=686171;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [COPY INTO "PLAYERS" /*                                           ]8;id=239725;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=116361;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */...]                         

[01/27/24 17:34:58] INFO     query execution done                                                     ]8;id=271193;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=120834;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=487181;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=951212;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [75]:
# fbref_lineups = fbref_lineups.merge(df_matches[['MATCH_ID', 'WS_MATCH_ID']], on="WS_MATCH_ID")

In [85]:
df_player_match = fbref_lineups[['WS_player_id', 'player','MATCH_ID', 'TEAM_FBREF_ID', 'WS_starting_position', 
                                 'FBREF_position','jersey_number','FBREF_minutes_played','FBREF_is_starter','WS_is_starter',
                                 'WS_minutes_played']]

In [86]:
df_player_match = df_player_match.rename({'WS_player_id':'PLAYER_WS_ID', 'player':'PLAYER_FBREF_NAME', 'WS_starting_position':'STARTING_POSITION_WS',
                        'FBREF_position':'POSITION_FBREF', 'jersey_number':'JERSEY_NUMBER', 'FBREF_minutes_played':'MINUTES_PLAYED_FBREF',
                        'FBREF_is_starter':'IS_STARTER_FBREF','WS_is_starter':'IS_STARTER_WS','WS_minutes_played':'MINUTES_PLAYED_WS'}, axis=1)

In [89]:
create_player_match_query = """
CREATE TABLE IF NOT EXISTS PLAYER_MATCH (
    PLAYER_WS_ID INT,
    PLAYER_FBREF_NAME VARCHAR(255),
    MATCH_ID VARCHAR(255),
    TEAM_FBREF_ID VARCHAR(255),
    STARTING_POSITION_WS VARCHAR(255),
    POSITION_FBREF VARCHAR(255),
    JERSEY_NUMBER INT,
    MINUTES_PLAYED_FBREF INT,
    MINUTES_PLAYED_WS INT,
    IS_STARTER_FBREF BOOLEAN,
    IS_STARTER_WS BOOLEAN,
    PRIMARY KEY (PLAYER_WS_ID, MATCH_ID),
    FOREIGN KEY (PLAYER_WS_ID) REFERENCES GEGENSTATS.TABLES.PLAYERS(PLAYER_WS_ID),
    FOREIGN KEY (MATCH_ID) REFERENCES GEGENSTATS.TABLES.MATCHES(MATCH_ID),
    FOREIGN KEY (TEAM_FBREF_ID) REFERENCES GEGENSTATS.TABLES.TEAMS(TEAM_FBREF_ID)
);
"""

In [90]:
cur.execute(create_player_match_query)

[01/27/24 17:37:12] INFO     query: [CREATE TABLE IF NOT EXISTS PLAYER_MATCH ( PLAYER_WS_ID INT,      ]8;id=899895;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=628859;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             PLAYER_FBREF_NAME VA...]                                                              

                    INFO     query execution done                                                     ]8;id=546140;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=950751;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=300356;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=281830;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [91]:
insert_to_snowflake_DB(['PLAYER_WS_ID, MATCH_ID'], 'PLAYER_MATCH', df_player_match, replace=True)

[01/27/24 17:37:29] INFO     query: [TRUNCATE TABLE PLAYER_MATCH]                                     ]8;id=335044;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=914601;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=133978;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=982497;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=731122;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=243817;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=455170;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=343238;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=366642;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=401683;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=275240;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=384934;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=631954;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=688805;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

[01/27/24 17:37:30] INFO     query: [COPY INTO "PLAYER_MATCH" /*                                      ]8;id=916116;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=45915;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas...]                              

[01/27/24 17:37:32] INFO     query execution done                                                     ]8;id=56634;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=557038;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=472253;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=860570;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

### Attempt to add shot events data!

In [87]:
fbref_shot_events = fbref.read_shot_events()

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:674: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[01/28/24 12:03:34] INFO     [1/969] Retrieving game with id=3adf2aa7                                 ]8;id=713990;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=390253;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

                    INFO     [2/969] Retrieving game with id=4eb36e37                                 ]8;id=820957;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=153464;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

                    INFO     [3/969] Retrieving game with id=6f454493                                 ]8;id=917945;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=354995;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

                    INFO     [4/969] Retrieving game with id=c99ebbf5                                 ]8;id=601811;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=245407;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

...

                    INFO     [965/969] Retrieving game with id=006fb5b5                               ]8;id=553599;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=275262;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

                    INFO     [966/969] Retrieving game with id=e0a9c631                               ]8;id=558637;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=863098;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

                    INFO     [967/969] Retrieving game with id=9a03e25c                               ]8;id=505796;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=429678;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

                    INFO     [968/969] Retrieving game with id=abd525b4                               ]8;id=615635;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=338073;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

                    INFO     [969/969] Retrieving game with id=35fb5bc2                               ]8;id=642934;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=731728;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1057\1057]8;;\

In [88]:
fbref_shot_events = fbref_shot_events.rename_axis(index={'season': 'SEASON', 'league': 'COMPETITION'})

In [89]:
fbref_shot_events = make_season_integer(fbref_shot_events)

In [90]:
# cur.execute('SELECT * FROM EVENTS_SPADL')
# team_rows = cur.fetchall()
# column_names = [desc[0] for desc in cur.description]
# ws_event_spadl = pd.DataFrame(team_rows, columns=column_names)

In [91]:
ws_event_spadl['TYPE_NAME'].unique()

array(['pass', 'clearance', 'keeper_claim', 'dribble', 'bad_touch',
       'shot', 'freekick_short', 'foul', 'take_on', 'interception',
       'freekick_crossed', 'cross', 'good_touch', 'goalkick', 'throw_in',
       'shot_freekick', 'keeper_save', 'keeper_pick_up', 'tackle',
       'keeper_punch', 'corner_crossed', 'corner_short', 'shot_penalty'],
      dtype=object)

In [113]:
ws_event_spadl['TIME_SECONDS'] = ws_event_spadl['TIME_SECONDS'].astype(int)
ws_event_spadl['PLAYER_WS_ID'] = ws_event_spadl['PLAYER_WS_ID'].astype(int)

In [77]:
ws_shots = ws_event_spadl[(ws_event_spadl['TYPE_NAME'] == 'shot') | (ws_event_spadl['TYPE_NAME'] == 'shot_freekick') | \
               (ws_event_spadl['TYPE_NAME'] == 'shot_penalty')]

In [96]:
fbref_shot_events.reset_index(inplace=True)

In [97]:
fbref_shot_events.columns = fbref_shot_events.columns.get_level_values(0) + fbref_shot_events.columns.get_level_values(1)

In [98]:
fbref_shot_events = fbref_shot_events.merge(fbref_schedule[['COMPETITION','SEASON','game','game_id','ws_game_id']], 
                        on=['COMPETITION','SEASON','game'])

In [326]:
# cur.execute('SELECT * FROM PLAYERS')
# player_rows = cur.fetchall()
# column_names = [desc[0] for desc in cur.description]
# df_players = pd.DataFrame(player_rows, columns=column_names)

[01/28/24 15:20:48] INFO     query: [SELECT * FROM PLAYERS]                                           ]8;id=203631;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=777833;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=628606;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=641986;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1175                                   ]8;id=818544;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=817040;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [101]:
fbref_shot_events.rename({'player':'PLAYER_FBREF_NAME'}, axis=1, inplace=True)

In [102]:
fbref_shot_events['PLAYER_FBREF_NAME'] = fbref_shot_events['PLAYER_FBREF_NAME'].str.replace(' \(pen\)', '', regex=True)

In [103]:
fbref_shot_events = fbref_shot_events.merge(df_players, on='PLAYER_FBREF_NAME', how="left")

In [104]:
fbref_shot_events.rename({'game_id':'MATCH_ID'}, axis=1, inplace=True)

In [341]:
import numpy as np

In [342]:
# rows_to_add = [
#     ['ENG-Premier League', 2324, '2023-12-02 Brentford-Luton Town', '27', 'Yehor Yarmoliuk','Brentford',0.04,np.nan,'Blocked',16,
#  'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,'0f71f535',1729547,444304,'Yehor Yarmoliuk'],
# ['ENG-Premier League', 2324, '2023-11-25 Brentford-Arsenal', "71", 'Yehor Yarmoliuk','Brentford',0.03,0.12,'Saved',27,
#  'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,'626c6561',1729535,444304,'Yehor Yarmoliuk'],
# ['ENG-Premier League', 2324, '2023-11-12 Liverpool-Brentford', "87", 'Yehor Yarmoliuk','Brentford',0.05,np.nan,'Off Target',21,
#  'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,'996ee990',1729245,444304,'Yehor Yarmoliuk'],
# ['ENG-Premier League', 2324, '2023-10-28 Chelsea-Brentford', "90", 'Yehor Yarmoliuk','Brentford',0.49,0.25,'Saved',11,
#  'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,'91e3b922',1729223,444304,'Yehor Yarmoliuk'],
# ['ENG-Premier League', 2324, '2023-10-21 Brentford-Burnley', "90+7", 'Yehor Yarmoliuk','Brentford',0.09,np.nan,'Off Target',8,
#  'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,'52781f37',1729211,444304,'Yehor Yarmoliuk'],
# ['ENG-Premier League', 2324, '2023-12-09 Sheffield Utd-Brentford', "51", 'Yehor Yarmoliuk','Brentford',0.02,0.02,'Saved',19,
#  'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,'e268f518',1729489,444304,'Yehor Yarmoliuk']
# ]

In [418]:
# for row in rows_to_add:
#     fbref_shot_events.loc[len(fbref_shot_events)] = row

C:\Users\ksbha\AppData\Local\Temp\ipykernel_8416\763870916.py:2: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  fbref_shot_events.loc[len(fbref_shot_events)] = row
C:\Users\ksbha\AppData\Local\Temp\ipykernel_8416\763870916.py:2: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  fbref_shot_events.loc[len(fbref_shot_events)] = row
C:\Users\ksbha\AppData\Local\Temp\ipykernel_8416\763870916.py:2: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a futur

In [347]:
# I'm going to drop Yarmolenko for now
ws_dropped_shots = ws_shots[ws_shots['PLAYER_WS_ID'] == 444304]
ws_shots = ws_shots[ws_shots['PLAYER_WS_ID'] != 444304]

In [ ]:
for game in ws_shots['MATCH_ID'].unique():
    if len(ws_shots.loc[ws_shots.MATCH_ID == game]) != len(fbref_shot_events.loc[fbref_shot_events.MATCH_ID == game]):
        print(game)

In [423]:
# fbref_shot_events[['new_minute', 'added_minute']] = fbref_shot_events['minute'].apply(
#     lambda x: pd.Series(str(x).split('+') if '+' in str(x) else [x, 0])
# )

In [424]:
fbref_shot_events['new_minute'] = fbref_shot_events['new_minute'].astype(int)
fbref_shot_events['added_minute'] = fbref_shot_events['added_minute'].astype(int)

In [425]:
fbref_shot_events = fbref_shot_events.sort_values(by=['MATCH_ID', 'new_minute', 'added_minute', 'PLAYER_WS_ID']).reset_index(drop=True)

In [322]:
ws_shots = ws_shots.sort_values(by=['MATCH_ID', 'PERIOD_ID','TIME_SECONDS', 'PLAYER_WS_ID']).reset_index(drop=True)

In [413]:
fbref_shot_events[ws_shots['PLAYER_WS_ID'] != fbref_shot_events['PLAYER_WS_ID']].head(50)

ValueError: Can only compare identically-labeled Series objects

In [324]:
ws_shots[ws_shots['PLAYER_WS_ID'] != fbref_shot_events['PLAYER_WS_ID']]

MATCH_ID  ORIGINAL_EVENT_ID  PERIOD_ID  TIME_SECONDS TEAM_FBREF_ID  \
67     006fb5b5       2.637216e+09          1        2404.0      18bb7c10   
68     006fb5b5       2.637217e+09          1        2456.0      47c64c55   
76     006fb5b5       2.637244e+09          2        1028.0      18bb7c10   
77     006fb5b5       2.637244e+09          2        1035.0      18bb7c10   
92     007b352e       2.605953e+09          1         300.0      8cec06e1   
...         ...                ...        ...           ...           ...   
24883  ff51efc7       2.319377e+09          1        2632.0      b8fd03ef   
24914  ffc59ea8       2.601299e+09          2        1288.0      fd962109   
24915  ffc59ea8       2.601300e+09          2        1319.0      fd962109   
24923  ffc59ea8       2.601380e+09          2        3481.0      1df6b87e   
24924  ffc59ea8       2.601381e+09          2        3531.0      fd962109   

       PLAYER_WS_ID  START_X    END_X  START_Y   END_Y  RESULT_ID  ACTION_ID  \
67           273257   93.555  105.000   44.608  23.800          0        567   
68            91822   30.135    2.520   35.428  33.728          0        575   
76           367185   85.050   97.650   32.980  33.252          0        909   
77           322036   84.945   86.415   33.932  34.000          0        913   
92           362758   13.545    1.470   29.104  32.912          0         98   
...             ...      ...      ...      ...     ...        ...        ...   
24883         19119   28.245    0.000   38.556  40.120          0        701   
24914        136824   88.935   90.720   29.104  29.308          0        841   
24915        134332   79.695  105.000   23.868  40.596          0        845   
24923        138695   13.755    0.945   30.124  33.048          0       1328   
24924         29463   81.375  103.110   45.764  35.564          0       1351   

      TYPE_NAME BODYPART_NAME  
67         shot     foot_left  
68         shot     foot_left  
76         shot     foot_left  
77         shot     foot_left  
92         shot     foot_left  
...         ...           ...  
24883      shot    foot_right  
24914      shot    foot_right  
24915      shot    foot_right  
24923      shot          head  
24924      shot    foot_right  

[2778 rows x 14 columns]

In [358]:
## I've hit a stumbling block- lining up my ws_shots and fbref_shots is a bit of a challenge having added Yarmolenko. 
## I need a Minute estiamte for the ws_events_spadl data

In [394]:
filtered_events = ws_event_spadl[['MATCH_ID', 'PERIOD_ID','TIME_SECONDS']].drop_duplicates()

In [395]:
filtered_events_period1 = filtered_events[filtered_events['PERIOD_ID'] == 1]
filtered_events_period2 = filtered_events[filtered_events['PERIOD_ID'] == 2]

In [397]:
start_time_2nd_half = filtered_events_period2.groupby(['MATCH_ID', 'PERIOD_ID'])['TIME_SECONDS'].min().reset_index()

In [ ]:
## Take it from here on 28th Jan 2024

In [408]:
for index, row in tqdm(start_time_2nd_half.iterrows()):
    time_to_remove = row['TIME_SECONDS']
    ws_event_spadl.loc[(ws_event_spadl['MATCH_ID'] == row['MATCH_ID']) & (ws_event_spadl['PERIOD_ID'] == 2), 'TIME_SECONDS'] -= time_to_remove

968it [02:46,  5.81it/s]


In [ ]:
## 2700 seconds in a half

In [117]:
# ws_dropped_shots = ws_shots[ws_shots['PLAYER_WS_ID'] == 444304]
# ws_shots = ws_shots[ws_shots['PLAYER_WS_ID'] != 444304]

In [ ]:
# for game in ws_shots['MATCH_ID'].unique():
#     if len(ws_shots.loc[ws_shots.MATCH_ID == game]) != len(fbref_shot_events.loc[fbref_shot_events.MATCH_ID == game]):
#         print(game)

In [ ]:
ws_shots['xG'] = np.nan
ws_shots['PSxG'] = np.nan
ws_shots['outcome'] = np.nan
ws_shots['distance'] = np.nan
ws_shots['body_part'] = np.nan
ws_shots['notes'] = np.nan
ws_shots['SCA 1player'] = np.nan
ws_shots['SCA 1event'] = np.nan
ws_shots['SCA 2player'] = np.nan
ws_shots['SCA 2event'] = np.nan
ws_shots['FBREF_PLAYER_WS_ID'] = np.nan
ws_shots['PLAYER_WS_NAME'] = np.nan

In [122]:
import numpy as np

In [181]:
fbref_shot_events.rename({'PLAYER_WS_ID':'FBREF_PLAYER_WS_ID'}, axis=1, inplace=True)

In [203]:
cols_of_interest = ['xG', 'PSxG', 'outcome', 'distance', 'body_part', 'notes', 'SCA 1player', 'SCA 1event', 
                    'SCA 2player', 'SCA 2event', 'FBREF_PLAYER_WS_ID', 'PLAYER_WS_NAME']
for game in ws_shots['MATCH_ID'].unique():
    df_hold = fbref_shot_events[fbref_shot_events['MATCH_ID'] == game]
    ind_list = ws_shots[ws_shots['MATCH_ID'] == game].sort_values(by='ACTION_ID', ascending=True).index
    ws_shots.loc[ind_list, cols_of_interest] = np.array(df_hold[cols_of_interest])

In [204]:
ws_shots['FBREF_PLAYER_WS_ID'] = ws_shots['FBREF_PLAYER_WS_ID'].astype(int)

In [210]:
mismatched_inds = ws_shots[ws_shots['PLAYER_WS_ID'] != ws_shots['FBREF_PLAYER_WS_ID']].index

In [240]:
for i in range(len(mismatched_inds) // 2):
    val1 = ws_shots.loc[mismatched_inds, cols_of_interest].iloc[2*i]
    val2 = ws_shots.loc[mismatched_inds, cols_of_interest].iloc[(2*i)+1]

    ws_shots.loc[val1.name, cols_of_interest] = np.array(val2)
    ws_shots.loc[val2.name, cols_of_interest] = np.array(val1)

In [241]:
ws_shots[ws_shots['PLAYER_WS_ID'] != ws_shots['FBREF_PLAYER_WS_ID']]

Empty DataFrame
Columns: [WS_MATCH_ID, ORIGINAL_EVENT_ID, PERIOD_ID, TIME_SECONDS, TEAM_WS_ID, PLAYER_WS_ID, START_X, END_X, START_Y, END_Y, type_id, RESULT_ID, bodypart_id, ACTION_ID, player, team, TYPE_NAME, BODYPART_NAME, MATCH_ID, TEAM_FBREF_ID, xG, PSxG, outcome, distance, body_part, notes, SCA 1player, SCA 1event, SCA 2player, SCA 2event, FBREF_PLAYER_WS_ID, PLAYER_WS_NAME]
Index: []

In [251]:
df_shots = ws_shots[['MATCH_ID','ACTION_ID','xG', 'PSxG', 'outcome', 'distance', 
          'body_part', 'notes', 'SCA 1player', 'SCA 1event', 'SCA 2player', 'SCA 2event']]

In [254]:
ws_dropped_shots[[cols_of_interest]] = np.nan

In [263]:
rows_to_add = [
    [0.04,np.nan,'Blocked',16,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
[0.03,0.12,'Saved',27,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
[0.05,np.nan,'Off Target',21,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
[0.49,0.25,'Saved',11,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
[0.09,np.nan,'Off Target',8,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
[0.02,0.02,'Saved',19,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk']
]

In [265]:
ws_dropped_shots[cols_of_interest] = np.array(rows_to_add)

In [268]:
ws_dropped_shots[['MATCH_ID','ACTION_ID','xG', 'PSxG', 'outcome', 'distance', 
          'body_part', 'notes', 'SCA 1player', 'SCA 1event', 'SCA 2player', 'SCA 2event']]

MATCH_ID  ACTION_ID    xG  PSxG     outcome distance   body_part  \
1392369  626c6561        975  0.04   nan     Blocked       16  Right Foot   
1397981  e268f518        877  0.03  0.12       Saved       27  Right Foot   
1398851  91e3b922       1541  0.05   nan  Off Target       21  Right Foot   
1400033  996ee990       1341  0.49  0.25       Saved       11  Right Foot   
1409070  0f71f535        447  0.09   nan  Off Target        8  Right Foot   
1411911  52781f37       1458  0.02  0.02       Saved       19  Right Foot   

        notes SCA 1player SCA 1event SCA 2player SCA 2event  
1392369   nan         nan        nan         nan        nan  
1397981   nan         nan        nan         nan        nan  
1398851   nan         nan        nan         nan        nan  
1400033   nan         nan        nan         nan        nan  
1409070   nan         nan        nan         nan        nan  
1411911   nan         nan        nan         nan        nan

In [275]:
df_shots = pd.concat([df_shots, ws_dropped_shots[['MATCH_ID','ACTION_ID','xG', 'PSxG', 'outcome', 'distance', 
          'body_part', 'notes', 'SCA 1player', 'SCA 1event', 'SCA 2player', 'SCA 2event']]]).sort_index()

In [279]:
df_shots.replace({"Jarrell Quansah": "Jarell Quansah"}, inplace=True)
df_shots.replace({"Omotayo Adaramola": "Tayo Adaramola"}, inplace=True)

In [296]:
df_shots.rename({'xG':'XG', 'PSxG':'PSXG', 'outcome':'OUTCOME', 'distance':'DISTANCE', 'body_part':'BODY_PART',
                 'notes':'NOTES', 'SCA 1player':'SCA_1_PLAYER_FBREF_NAME', 'SCA 1event':'SCA_1_PLAYER_FBREF_EVENT',
                 'SCA 2player':'SCA_2_PLAYER_FBREF_NAME', 'SCA 2event':'SCA_2_PLAYER_FBREF_EVENT'}, axis=1, inplace=True)

In [327]:
df_players.rename({'PLAYER_FBREF_NAME':'SCA_1_PLAYER_FBREF_NAME'}, axis=1, inplace=True)
df_players.rename({'PLAYER_WS_ID':'SCA_1_PLAYER_FBREF_ID'}, axis=1, inplace=True)

In [328]:
df_shots = df_shots.merge(df_players[['SCA_1_PLAYER_FBREF_ID','SCA_1_PLAYER_FBREF_NAME']], on='SCA_1_PLAYER_FBREF_NAME', how='left')

In [329]:
df_players.rename({'SCA_1_PLAYER_FBREF_NAME':'SCA_2_PLAYER_FBREF_NAME'}, axis=1, inplace=True)
df_players.rename({'SCA_1_PLAYER_FBREF_ID':'SCA_2_PLAYER_FBREF_ID'}, axis=1, inplace=True)

In [330]:
df_shots = df_shots.merge(df_players[['SCA_2_PLAYER_FBREF_ID','SCA_2_PLAYER_FBREF_NAME']], on='SCA_2_PLAYER_FBREF_NAME', how='left')

In [333]:
df_shots = df_shots.drop(['SCA_1_PLAYER_FBREF_NAME', 'SCA_2_PLAYER_FBREF_NAME'], axis=1)

In [335]:
df_shots.rename({'SCA_1_PLAYER_FBREF_ID':'SCA_1_PLAYER_WS_ID', 'SCA_2_PLAYER_FBREF_ID':'SCA_2_PLAYER_WS_ID'}, 
                axis=1, inplace=True)

In [336]:
create_shots_query = """
CREATE TABLE IF NOT EXISTS SHOT_EVENTS (
    MATCH_ID VARCHAR(255),
    ACTION_ID INT,
    XG DOUBLE,
    PSXG DOUBLE,
    OUTCOME VARCHAR(255),
    DISTANCE INT,
    BODY_PART VARCHAR(255),
    NOTES VARCHAR(255),
    SCA_1_PLAYER_WS_ID INT,
    SCA_1_PLAYER_FBREF_EVENT VARCHAR(255),
    SCA_2_PLAYER_WS_ID INT,
    SCA_2_PLAYER_FBREF_EVENT VARCHAR(255),
    PRIMARY KEY (MATCH_ID, ACTION_ID),
    FOREIGN KEY (MATCH_ID) REFERENCES GEGENSTATS.TABLES.MATCHES(MATCH_ID),
    FOREIGN KEY (MATCH_ID, ACTION_ID) REFERENCES GEGENSTATS.TABLES.EVENTS_SPADL(MATCH_ID, ACTION_ID),
    FOREIGN KEY (SCA_1_PLAYER_WS_ID) REFERENCES GEGENSTATS.TABLES.PLAYERS(PLAYER_WS_ID),
    FOREIGN KEY (SCA_2_PLAYER_WS_ID) REFERENCES GEGENSTATS.TABLES.PLAYERS(PLAYER_WS_ID)
);
"""

In [337]:
cur.execute(create_shots_query)

[01/28/24 15:25:39] INFO     query: [CREATE TABLE IF NOT EXISTS SHOT_EVENTS ( MATCH_ID VARCHAR(255),  ]8;id=506487;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=805529;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             ACTION_ID INT, X...]                                                                  

[01/28/24 15:25:40] INFO     query execution done                                                     ]8;id=702431;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=786791;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=821676;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=456092;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [339]:
df_shots.dtypes

MATCH_ID                     object
ACTION_ID                     int64
XG                           object
PSXG                         object
OUTCOME                      object
DISTANCE                     object
BODY_PART                    object
NOTES                        object
SCA_1_PLAYER_FBREF_EVENT     object
SCA_2_PLAYER_FBREF_EVENT     object
SCA_1_PLAYER_WS_ID          float64
SCA_2_PLAYER_WS_ID          float64
dtype: object

In [345]:
df_shots.replace({pd.NA: np.nan}, inplace=True)

In [348]:
df_shots['XG'] = df_shots['XG'].astype(float)
df_shots['PSXG'] = df_shots['PSXG'].astype(float)
df_shots['DISTANCE'] = df_shots['DISTANCE'].astype(int)
# df_shots['SCA_1_PLAYER_WS_ID'] = df_shots['SCA_1_PLAYER_WS_ID'].astype(int)
# df_shots['SCA_2_PLAYER_WS_ID'] = df_shots['SCA_2_PLAYER_WS_ID'].astype(int)

In [349]:
insert_to_snowflake_DB(['MATCH_ID', 'ACTION_ID'], 'SHOT_EVENTS', df_shots, replace=True)

[01/28/24 15:32:44] INFO     query: [TRUNCATE TABLE SHOT_EVENTS]                                      ]8;id=616254;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=79008;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

[01/28/24 15:32:45] INFO     query execution done                                                     ]8;id=464189;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=575352;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=220775;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=920101;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=743166;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=815505;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=533389;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=176676;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=945552;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=9847;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=738997;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=339179;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

[01/28/24 15:32:46] INFO     query: [COPY INTO "SHOT_EVENTS" /*                                       ]8;id=569024;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=368953;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas(...]                             

[01/28/24 15:32:48] INFO     query execution done                                                     ]8;id=471334;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=822450;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=439505;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=620328;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [387]:
spadl.add_names

<function socceraction.spadl.utils.add_names(actions: pandera.typing.pandas.DataFrame[socceraction.spadl.schema.SPADLSchema]) -> pandera.typing.pandas.DataFrame[socceraction.spadl.schema.SPADLSchema]>

In [396]:
testo = ws_event_spadl[ws_event_spadl['MATCH_ID'] == 'b513d9fe'].copy()

In [401]:
testo.rename({'TEAM_FBREF_ID':'team_id '}, axis=1)

WS_MATCH_ID ORIGINAL_EVENT_ID  PERIOD_ID  TIME_SECONDS  TEAM_WS_ID  \
0          1640701        2449373449          1             0         167   
1          1640701        2449373505          1             3         167   
2          1640701        2449373529          1             6         167   
3          1640701        2449373569          1            10         167   
4          1640701        2449373591          1            13         167   
...            ...               ...        ...           ...         ...   
97917      1640701        2449456637          2          3394          23   
97918      1640701        2449456701          2          3401          23   
97919      1640701        2449456941          2          3431          23   
97920      1640701        2449457035          2          3440          23   
97921      1640701        2449457299          2          3469          23   

       PLAYER_WS_ID  START_X   END_X  START_Y   END_Y  type_id  RESULT_ID  \
0            315227   52.290  73.815   34.000  26.860        0          1   
1            122945   71.085  70.035   27.064  59.976        0          1   
2            101374   70.350  95.760   58.072  45.016        0          1   
3            121774   95.760  82.530   44.880  62.628        0          1   
4            101374   82.005  81.690   63.036  56.644        0          1   
...             ...      ...     ...      ...     ...      ...        ...   
97917         83078   11.235  24.255   41.140  43.656       18          1   
97918        105720    4.725   4.725   20.876  20.876       17          1   
97919        105720   13.020  62.370   45.288  38.964        0          0   
97920        379732   23.100  73.080   54.332  51.952        0          0   
97921        105720   10.815  10.815   30.872  30.872       15          1   

       bodypart_id  ACTION_ID           player             team  \
0                0          0   Erling Haaland  Manchester City   
1                0          1       Nathan Aké  Manchester City   
2                0          2      John Stones  Manchester City   
3                0          3          Ederson  Manchester City   
4                0          4      John Stones  Manchester City   
...            ...        ...              ...              ...   
97917            1       1427  Kieran Trippier    Newcastle Utd   
97918            0       1429        Nick Pope    Newcastle Utd   
97919            0       1430        Nick Pope    Newcastle Utd   
97920            0       1433      Sven Botman    Newcastle Utd   
97921            0       1445        Nick Pope    Newcastle Utd   

            TYPE_NAME BODYPART_NAME  MATCH_ID  team_id   
0                pass          foot  b513d9fe  b8fd03ef  
1                pass          foot  b513d9fe  b8fd03ef  
2                pass          foot  b513d9fe  b8fd03ef  
3                pass          foot  b513d9fe  b8fd03ef  
4                pass          foot  b513d9fe  b8fd03ef  
...               ...           ...       ...       ...  
97917       clearance          head  b513d9fe  b2b47a98  
97918  keeper_pick_up          foot  b513d9fe  b2b47a98  
97919            pass          foot  b513d9fe  b2b47a98  
97920            pass          foot  b513d9fe  b2b47a98  
97921    keeper_claim          foot  b513d9fe  b2b47a98  

[1446 rows x 20 columns]

In [404]:
spadl.play_left_to_right(testo.rename({'TEAM_FBREF_ID':'team_id','START_X':'start_x','START_Y':'start_y',
                                       'END_X':'end_x','END_Y':'end_y'}, axis=1),'b2b47a98')

WS_MATCH_ID ORIGINAL_EVENT_ID  PERIOD_ID  TIME_SECONDS  TEAM_WS_ID  \
0          1640701        2449373449          1             0         167   
1          1640701        2449373505          1             3         167   
2          1640701        2449373529          1             6         167   
3          1640701        2449373569          1            10         167   
4          1640701        2449373591          1            13         167   
...            ...               ...        ...           ...         ...   
97917      1640701        2449456637          2          3394          23   
97918      1640701        2449456701          2          3401          23   
97919      1640701        2449456941          2          3431          23   
97920      1640701        2449457035          2          3440          23   
97921      1640701        2449457299          2          3469          23   

       PLAYER_WS_ID  start_x   end_x  start_y   end_y  type_id  RESULT_ID  \
0            315227   52.710  31.185   34.000  41.140        0          1   
1            122945   33.915  34.965   40.936   8.024        0          1   
2            101374   34.650   9.240    9.928  22.984        0          1   
3            121774    9.240  22.470   23.120   5.372        0          1   
4            101374   22.995  23.310    4.964  11.356        0          1   
...             ...      ...     ...      ...     ...      ...        ...   
97917         83078   11.235  24.255   41.140  43.656       18          1   
97918        105720    4.725   4.725   20.876  20.876       17          1   
97919        105720   13.020  62.370   45.288  38.964        0          0   
97920        379732   23.100  73.080   54.332  51.952        0          0   
97921        105720   10.815  10.815   30.872  30.872       15          1   

       bodypart_id  ACTION_ID           player             team  \
0                0          0   Erling Haaland  Manchester City   
1                0          1       Nathan Aké  Manchester City   
2                0          2      John Stones  Manchester City   
3                0          3          Ederson  Manchester City   
4                0          4      John Stones  Manchester City   
...            ...        ...              ...              ...   
97917            1       1427  Kieran Trippier    Newcastle Utd   
97918            0       1429        Nick Pope    Newcastle Utd   
97919            0       1430        Nick Pope    Newcastle Utd   
97920            0       1433      Sven Botman    Newcastle Utd   
97921            0       1445        Nick Pope    Newcastle Utd   

            TYPE_NAME BODYPART_NAME  MATCH_ID   team_id  
0                pass          foot  b513d9fe  b8fd03ef  
1                pass          foot  b513d9fe  b8fd03ef  
2                pass          foot  b513d9fe  b8fd03ef  
3                pass          foot  b513d9fe  b8fd03ef  
4                pass          foot  b513d9fe  b8fd03ef  
...               ...           ...       ...       ...  
97917       clearance          head  b513d9fe  b2b47a98  
97918  keeper_pick_up          foot  b513d9fe  b2b47a98  
97919            pass          foot  b513d9fe  b2b47a98  
97920            pass          foot  b513d9fe  b2b47a98  
97921    keeper_claim          foot  b513d9fe  b2b47a98  

[1446 rows x 20 columns]

In [390]:
ws_event_spadl[ws_event_spadl['MATCH_ID'] == 'b513d9fe']

WS_MATCH_ID ORIGINAL_EVENT_ID  PERIOD_ID  TIME_SECONDS  TEAM_WS_ID  \
0          1640701        2449373449          1             0         167   
1          1640701        2449373505          1             3         167   
2          1640701        2449373529          1             6         167   
3          1640701        2449373569          1            10         167   
4          1640701        2449373591          1            13         167   
...            ...               ...        ...           ...         ...   
97917      1640701        2449456637          2          3394          23   
97918      1640701        2449456701          2          3401          23   
97919      1640701        2449456941          2          3431          23   
97920      1640701        2449457035          2          3440          23   
97921      1640701        2449457299          2          3469          23   

       PLAYER_WS_ID  START_X   END_X  START_Y   END_Y  type_id  RESULT_ID  \
0            315227   52.290  73.815   34.000  26.860        0          1   
1            122945   71.085  70.035   27.064  59.976        0          1   
2            101374   70.350  95.760   58.072  45.016        0          1   
3            121774   95.760  82.530   44.880  62.628        0          1   
4            101374   82.005  81.690   63.036  56.644        0          1   
...             ...      ...     ...      ...     ...      ...        ...   
97917         83078   11.235  24.255   41.140  43.656       18          1   
97918        105720    4.725   4.725   20.876  20.876       17          1   
97919        105720   13.020  62.370   45.288  38.964        0          0   
97920        379732   23.100  73.080   54.332  51.952        0          0   
97921        105720   10.815  10.815   30.872  30.872       15          1   

       bodypart_id  ACTION_ID           player             team  \
0                0          0   Erling Haaland  Manchester City   
1                0          1       Nathan Aké  Manchester City   
2                0          2      John Stones  Manchester City   
3                0          3          Ederson  Manchester City   
4                0          4      John Stones  Manchester City   
...            ...        ...              ...              ...   
97917            1       1427  Kieran Trippier    Newcastle Utd   
97918            0       1429        Nick Pope    Newcastle Utd   
97919            0       1430        Nick Pope    Newcastle Utd   
97920            0       1433      Sven Botman    Newcastle Utd   
97921            0       1445        Nick Pope    Newcastle Utd   

            TYPE_NAME BODYPART_NAME  MATCH_ID TEAM_FBREF_ID  
0                pass          foot  b513d9fe      b8fd03ef  
1                pass          foot  b513d9fe      b8fd03ef  
2                pass          foot  b513d9fe      b8fd03ef  
3                pass          foot  b513d9fe      b8fd03ef  
4                pass          foot  b513d9fe      b8fd03ef  
...               ...           ...       ...           ...  
97917       clearance          head  b513d9fe      b2b47a98  
97918  keeper_pick_up          foot  b513d9fe      b2b47a98  
97919            pass          foot  b513d9fe      b2b47a98  
97920            pass          foot  b513d9fe      b2b47a98  
97921    keeper_claim          foot  b513d9fe      b2b47a98  

[1446 rows x 20 columns]